In [106]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [107]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [108]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/FinancialProgressReport/finProgress_newRpt.aspx"
params = {
    'params': 0
}
for key, value in params.items():
    url = url #+ "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [109]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddl_finYear'
iay_radio_name = 'ctl00$ContentPlaceHolder1$rdlScheme'
excel_button = 'ctl00$ContentPlaceHolder1$btnExport'
content_table_class = 'table_s'

In [110]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

def check_table():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.CSS_SELECTOR, '.'+content_table_class))            
    WebDriverWait(driver, 2).until(element_present)
    
#Check Submit button
def delete_excel():
    driver.execute_script("return document.getElementsByName('" + excel_button + "')[0].remove()")
def check_excel():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, excel_button ) ) )

In [111]:
#Start Chrome
driver.get(url)
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[0:1]
print(yearlist)
for year in yearlist:
    print("--Scrapping data for Year: ", year['text'])
    #Start Chrome
    driver.get(url)
    #Year Selection
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(".//option[@value='0']").click()
    year_query = ".//option[@value='" + year['value'] + "']"
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    
    #DataStore
    df_list = []
    
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, iay_radio_name))
    )
    element.click()
    
    #state select
    check_table()
    temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[3:-2]
    states = []
    for row in temp_list:
        try:
            x = {}
            td = row.find_elements_by_xpath(".//td")[1]
            x['name'] = td.text
            x['link'] = td.find_element_by_tag_name("a").get_attribute("href")
            states.append(x)
        except Exception as e:
            print("Error while parsing table data |", e)
    for state in states:
        print("----Scrapping data for State: ", state['name'])
        driver.get(state['link'])
        check_table()
        temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
        districts = []
        for row in temp_list:
            x = {}            
            x['name'] = row.find_elements_by_xpath(".//td")[1].text
            x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
            districts.append(x)
        for district in districts:
            print("------Scrapping data for District: ", district['name'])
            driver.get(district['link'])
            check_table()
            temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
            blocks = []
            for row in temp_list:
                x = {}            
                x['name'] = row.find_elements_by_xpath(".//td")[1].text
                x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
                blocks.append(x)
            
            for block in blocks:
                print("--------Scrapping data for Block: ", block['name'])
                driver.get(block['link'])
                check_table()
                html_table = driver.find_element_by_class_name(content_table_class).get_attribute('outerHTML')
                df = pd.read_html(html_table, header=3)[0]
                df = df[:-1]
                #df.columns = table_head
                df['Financial Year'] = year['text']
                df['State Name'] = state['name']
                df['District Name'] = district['name']
                df['Block Name'] = block['name']
                df_list.append(df)
                #except Exception as e:
                #    print("Error while table data |", e)
                
    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df.drop(df.columns[0],axis=1,inplace=True)
    df = df.reset_index()
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

[{'text': '2010-2011', 'value': '2010-2011 '}]
--Scrapping data for Year:  2010-2011
Error while parsing table data | Message: no such element: Unable to locate element: {"method":"tag name","selector":"a"}
  (Session info: chrome=66.0.3359.181)
  (Driver info: chromedriver=2.35.528161 (5b82f2d2aae0ca24b877009200ced9065a772e73),platform=Windows NT 10.0.17134 x86_64)

----Scrapping data for State:  ARUNACHAL PRADESH
----Scrapping data for State:  ASSAM
------Scrapping data for District:  BARPETA
--------Scrapping data for Block:  RUPSHI
------Scrapping data for District:  DHEMAJI
--------Scrapping data for Block:  MURKONGSELEK
------Scrapping data for District:  KARIMGANJ
--------Scrapping data for Block:  BADARPUR
------Scrapping data for District:  NAGAON
--------Scrapping data for Block:  Jugijan
------Scrapping data for District:  SONITPUR
--------Scrapping data for Block:  BEHALI
--------Scrapping data for Block:  BIHAGURI
----Scrapping data for State:  BIHAR
------Scrapping data f

--------Scrapping data for Block:  LAXMIPUR
--------Scrapping data for Block:  SIKANDRA
--------Scrapping data for Block:  SONO
------Scrapping data for District:  JEHANABAD
--------Scrapping data for Block:  GHOSHI
--------Scrapping data for Block:  HULASGANJ
--------Scrapping data for Block:  JEHANABAD
--------Scrapping data for Block:  KAKO
--------Scrapping data for Block:  MAKHDUMPUR
--------Scrapping data for Block:  MODANGANJ
--------Scrapping data for Block:  RATNI FARIDPUR
------Scrapping data for District:  KAIMUR (BHABUA)
--------Scrapping data for Block:  ADHAURA
--------Scrapping data for Block:  BHABUA
--------Scrapping data for Block:  BHAGWANPUR
--------Scrapping data for Block:  CHAINPUR
--------Scrapping data for Block:  CHAND
--------Scrapping data for Block:  DURGAWATI
--------Scrapping data for Block:  KUDRA
--------Scrapping data for Block:  MOHANIA
--------Scrapping data for Block:  NUAON
--------Scrapping data for Block:  RAMGARH
--------Scrapping data for Block

--------Scrapping data for Block:  BIKRAM
--------Scrapping data for Block:  DANAPUR
--------Scrapping data for Block:  DANIYAWAN
--------Scrapping data for Block:  DHANARUA
--------Scrapping data for Block:  DULHINBAZAR
--------Scrapping data for Block:  FATUHA
--------Scrapping data for Block:  GHOSWARI
--------Scrapping data for Block:  KHUSRUPUR
--------Scrapping data for Block:  MANER
--------Scrapping data for Block:  MASAURHI
--------Scrapping data for Block:  MOKAMA
--------Scrapping data for Block:  NAUBATPUR
--------Scrapping data for Block:  PALIGANJ
--------Scrapping data for Block:  PANDARKH
--------Scrapping data for Block:  PATNA SADAR
--------Scrapping data for Block:  PHULWARI
--------Scrapping data for Block:  PUNPUN
--------Scrapping data for Block:  SAMPATCHAK
------Scrapping data for District:  PURBI CHAMPARAN
--------Scrapping data for Block:  ADAPUR
--------Scrapping data for Block:  ARERAJ
--------Scrapping data for Block:  Banjariya
--------Scrapping data for B

--------Scrapping data for Block:  raghopur
--------Scrapping data for Block:  SARAIGARH
--------Scrapping data for Block:  SUPAUL
--------Scrapping data for Block:  TRIVENIGANJ
------Scrapping data for District:  VAISHALI
--------Scrapping data for Block:  BAGHWANPUR
--------Scrapping data for Block:  BIDUPUR
--------Scrapping data for Block:  CHEHRAKALA
--------Scrapping data for Block:  DESRI
--------Scrapping data for Block:  GAROUL
--------Scrapping data for Block:  HAJIPUR
--------Scrapping data for Block:  JANDAHA
--------Scrapping data for Block:  LALGANJ
--------Scrapping data for Block:  MAHNAR
--------Scrapping data for Block:  MAHUA
--------Scrapping data for Block:  PATEDHI BELSAR
--------Scrapping data for Block:  PATEPUR
--------Scrapping data for Block:  RAGHOPUR
--------Scrapping data for Block:  RAJAPAKAR
--------Scrapping data for Block:  SAHDEI
--------Scrapping data for Block:  VAISHALI
----Scrapping data for State:  CHHATTISGARH
----Scrapping data for State:  GOA


--------Scrapping data for Block:  Tundi
------Scrapping data for District:  DUMKA
--------Scrapping data for Block:  DUMKA
--------Scrapping data for Block:  JARMUNDI
------Scrapping data for District:  EAST SINGHBUM
--------Scrapping data for Block:  BAHRAGORA
--------Scrapping data for Block:  Boram
--------Scrapping data for Block:  DHALBHUMGARH
--------Scrapping data for Block:  DUMARIA
--------Scrapping data for Block:  GOLMURI CUM JUGSALAI
--------Scrapping data for Block:  MUSABANI
--------Scrapping data for Block:  PATAMDA
--------Scrapping data for Block:  POTKA
------Scrapping data for District:  GARHWA
--------Scrapping data for Block:  BARDIHA
--------Scrapping data for Block:  BHAWNATHPUR
--------Scrapping data for Block:  BISHUNPURA
--------Scrapping data for Block:  CHINIA
--------Scrapping data for Block:  DANDA
--------Scrapping data for Block:  DANDAI
--------Scrapping data for Block:  GARHWA
--------Scrapping data for Block:  KETAR
--------Scrapping data for Block: 

--------Scrapping data for Block:  Vazhakulam
--------Scrapping data for Block:  Vypin
------Scrapping data for District:  IDUKKI
--------Scrapping data for Block:  Adimali
--------Scrapping data for Block:  Azhutha
--------Scrapping data for Block:  Devikulam
--------Scrapping data for Block:  Elamdesom
--------Scrapping data for Block:  Idukki
--------Scrapping data for Block:  Kattappana
--------Scrapping data for Block:  Nedumkandom
--------Scrapping data for Block:  Thodupuzha
------Scrapping data for District:  KANNUR
--------Scrapping data for Block:  Edakkad
--------Scrapping data for Block:  Irikkur
--------Scrapping data for Block:  Iritty
--------Scrapping data for Block:  Kuthuparamba
--------Scrapping data for Block:  Payyanur
--------Scrapping data for Block:  Peravoor
--------Scrapping data for Block:  Taliparamba
--------Scrapping data for Block:  Thalasseri
------Scrapping data for District:  KASARGOD
--------Scrapping data for Block:  KANHANGAD
--------Scrapping data 

--------Scrapping data for Block:  PUNASA
------Scrapping data for District:  MANDLA
--------Scrapping data for Block:  NARAYANGANJ
------Scrapping data for District:  MANDSAUR
--------Scrapping data for Block:  Mandsaur
------Scrapping data for District:  MORENA
--------Scrapping data for Block:  MORENA
--------Scrapping data for Block:  PAHADGARH
------Scrapping data for District:  NARSINGHPUR
--------Scrapping data for Block:  Babai Chichli
--------Scrapping data for Block:  Narsimhapur
------Scrapping data for District:  NEEMUCH
--------Scrapping data for Block:  Manasa
------Scrapping data for District:  RAISEN
--------Scrapping data for Block:  BADI
------Scrapping data for District:  RAJGARH
--------Scrapping data for Block:  RAJGARH
------Scrapping data for District:  RATLAM
--------Scrapping data for Block:  Jaora
--------Scrapping data for Block:  Piploda
------Scrapping data for District:  REWA
--------Scrapping data for Block:  GANGEV
--------Scrapping data for Block:  RAIP

--------Scrapping data for Block:  LANJA
--------Scrapping data for Block:  RATNAGIRI
--------Scrapping data for Block:  SANGAMESHWAR
------Scrapping data for District:  SANGLI
--------Scrapping data for Block:  JATH
--------Scrapping data for Block:  MIRAJ
--------Scrapping data for Block:  TASGAON
--------Scrapping data for Block:  WALWA
------Scrapping data for District:  SATARA
--------Scrapping data for Block:  KOREGAON
--------Scrapping data for Block:  SATARA
--------Scrapping data for Block:  WAI
------Scrapping data for District:  SINDHUDURG
--------Scrapping data for Block:  DEVGAD
------Scrapping data for District:  SOLAPUR
--------Scrapping data for Block:  AKKALKOT
--------Scrapping data for Block:  BARSHI
--------Scrapping data for Block:  KARMALA
--------Scrapping data for Block:  MADHA
--------Scrapping data for Block:  MALSHIRAS
--------Scrapping data for Block:  MANGALVEDHE
--------Scrapping data for Block:  MOHOL
--------Scrapping data for Block:  PANDHARPUR
--------

--------Scrapping data for Block:  BHADAR
--------Scrapping data for Block:  JAGDISHPUR
--------Scrapping data for Block:  MUSAFIR KHANA
--------Scrapping data for Block:  SANGRAMPUR
--------Scrapping data for Block:  SHUKUL BAZAR
------Scrapping data for District:  CHITRAKOOT
--------Scrapping data for Block:  PAHARI
------Scrapping data for District:  ETAH
--------Scrapping data for Block:  ALIGANJ
--------Scrapping data for Block:  SAKIT
------Scrapping data for District:  ETAWAH
--------Scrapping data for Block:  BASREHAR
--------Scrapping data for Block:  BHARTHANA
--------Scrapping data for Block:  TAKHA
------Scrapping data for District:  FAIZABAD
--------Scrapping data for Block:  AMANIGANJ
--------Scrapping data for Block:  SOHAWAL
------Scrapping data for District:  FARRUKHABAD
--------Scrapping data for Block:  KAMALGANJ
--------Scrapping data for Block:  MOHAMADABAD
------Scrapping data for District:  FIROZABAD
--------Scrapping data for Block:  EKA
--------Scrapping data f

----Scrapping data for State:  ANDAMAN AND NICOBAR
----Scrapping data for State:  DADRA AND NAGAR HAVELI
----Scrapping data for State:  DAMAN AND DIU
----Scrapping data for State:  LAKSHADWEEP
----Scrapping data for State:  PUDUCHERRY
----Scrapping data for State:  ANDHRA PRADESH
------Scrapping data for District:  ADILABAD
--------Scrapping data for Block:  Adilabad
----Scrapping data for State:  KARNATAKA
----Scrapping data for State:  TELANGANA
